# Cybernetic Game Theory


In [1]:
# THIS IS ACTIVELY W.I.P. August-October 2020.  Began transforming sketch into functions.  
# Instead of deleting sketch work, I am just commenting out to preserve thought process.
# Next step is to separate out functions and create new notebook/script to continue development.

# This notebook aims to illustrate a toy model of a cybernetic regulator along the lines of W.R. Ashby's work.
# It is instructive to see the game-theoretic foundations of other popular regulators, like Artificial Neural Networks.
# The regulator can "learn" a probability distribution of disturbances, using reinforcement learning.
# The result is effective control, channeling the flow of information from the environment into desired outcomes (states).

In [2]:
import numpy as np
import pandas as pd

In [3]:
# Create a game matrix for two players: Environment and Regulator
# Choose a goal for Regulator
# Environment goes first (row_i)
# Regulator goes second (column_j)
# Outcome is matrix element m_ij

In [4]:
#game_matrix = np.random.randint(10, size=(7,5))
#game_matrix

In [5]:
# Rows are plays (a.k.a. "disturbances") for the environment.  
# Create vector to use for pandas index and later to link up with probabilities.
def create_game(size):
    game_matrix = np.random.randint(10, size=size)
    rows = [i+1 for i in range(len(game_matrix))]
    print(rows)
    return pd.DataFrame(data = game_matrix, columns=[i+1 for i in range(game_matrix.shape[1])], index=rows)


In [6]:
game = create_game((7,12))
game

[1, 2, 3, 4, 5, 6, 7]


1   2   3   4   5   6   7   8   9   10  11  12
1   7   6   4   7   8   2   4   3   8   8   2   8
2   8   3   3   1   4   3   6   5   4   4   6   1
3   0   9   8   7   6   6   5   8   0   7   0   0
4   0   5   8   4   1   2   6   7   5   7   7   1
5   3   6   5   2   0   0   3   6   3   3   9   4
6   3   8   9   0   4   7   6   5   7   4   7   6
7   5   2   8   1   5   2   9   4   8   7   9   9

# Environment chooses play (row)

In [7]:
# Create distribution for environmental "plays" or "disturbances".
#dist = np.random.dirichlet(alpha=rows)

In [8]:
# Check that we have probabilities summing to 1.
#print(dist)
#sum(dist)

In [9]:
# Choose a play.  Distribution of environment must remain constant!
# There must be something to learn, and if dist is changing, the world is random.
def environment_play(game,dist):
    '''
    
    '''
    return np.random.choice(game.index, size=1, p=dist).item()

In [10]:
dist = np.random.dirichlet(alpha=game.index)
env_play = environment_play(game,dist)
env_play

6

# Regulator chooses action (column)

In [11]:
# We can use a Polya urn instead to define probabilities of actions for the regulator.
urn = np.random.randint(10, size=len(game.columns))
urn

array([4, 2, 2, 6, 9, 4, 4, 2, 1, 8, 6, 9])

In [12]:
# Probabilities of drawing from urn
probs = np.array([(i/sum(urn)) for i in urn])
probs

array([0.07017544, 0.03508772, 0.03508772, 0.10526316, 0.15789474,
       0.07017544, 0.07017544, 0.03508772, 0.01754386, 0.14035088,
       0.10526316, 0.15789474])

In [13]:
sum(probs)

0.9999999999999998

In [21]:
# Choose random draws from plays in the urn with probabilities according to the composition of the urn.
# We actually just care to draw from the plays, and not from the urn itself, although the urn is what will be updated/reinforced.
def regulator_action(game,probs):
    return np.random.choice(game.columns, size=1, p=probs).item()


In [22]:
reg_action = regulator_action(game,probs)
reg_action

4

# Update/Reinforce the action of the regulator.

In [23]:
# Use .item to get the value from the game table out of the locations (rows/columns) encoded in arrays.
out = game.loc[env_play,reg_action]
out

0

In [24]:
# Convince yourself that this row/column outcome corresponds to the game.
game

1   2   3   4   5   6   7   8   9   10  11  12
1   7   6   4   7   8   2   4   3   8   8   2   8
2   8   3   3   1   4   3   6   5   4   4   6   1
3   0   9   8   7   6   6   5   8   0   7   0   0
4   0   5   8   4   1   2   6   7   5   7   7   1
5   3   6   5   2   0   0   3   6   3   3   9   4
6   3   8   9   0   4   7   6   5   7   4   7   6
7   5   2   8   1   5   2   9   4   8   7   9   9

In [25]:
#  We need to set a goal for the regulator to achieve.
goal = 8

In [26]:
# Define regulator as dictionary of plays and associated probabilities.
regulator = dict(zip(game.columns,urn))
regulator

{1: 4, 2: 2, 3: 2, 4: 6, 5: 9, 6: 4, 7: 4, 8: 2, 9: 1, 10: 8, 11: 6, 12: 9}

In [27]:
# Compare outcome with goal, and reinforce (increase probability) action which regulator took in response to environment.
# It makes sense to reinforce individual successes more than we weaken, since we expect to fail a lot in the beginning.
# Try adding len(regulator), although this may be impractical for some examples.
#if out == goal:
#    print("success: reinforced the regulator's action", reg_action, "from", regulator[reg_action], "to", regulator[reg_action] + len(regulator))
#    regulator[reg_action] += len(regulator)
#    print('now we need to recalculate the probabilities according to the reinforced urn')
#else: print('fail')

In [28]:
# Confirm updated urn.
#regulator

In [29]:
# Recalculate probabilities and confirm that correct play increases in probability and all others go down.
def prob_calc(regulator_dict):
    sum_reg = np.array(sum([regulator_dict[i] for i in regulator_dict]))
    return np.array([regulator_dict[i]/sum_reg for i in regulator_dict])
    #sum(updated_probs),updated_probs

In [30]:
#prob_calc(regulator)

In [31]:
# Original probs
#probs

In [32]:
# We also want the regulator to update when it fails.  How might this look?
# Remember that the regulator's action distribution was random (the composition of the urn).  
# Consider that the regulator was perhaps overconfident, how can we make the "urn" less "confident"?
# Lets "sqeeze" the distribution in the urn, by making it less confident for any particular action.

# We could make drastic changes to our distribution, but we should keep in mind that we may want to use 
# the same fail-update procedure over and over again in an automated learning process.  
# If our "squeeze" is too drastic (e.g. making the urn parts equal / probabilities uniform) then even if
# our regulator is "learned" but makes a mistake, it will "forget" the learned distribution.

# We can still use the mean of the urn composition in a function that slightly squeezes, 
# incrementing those actions which are below the mean, and decrementing those below.

In [52]:
# FIX: IS SQUEEZING ALWAYS WORKING PROPERLY?  NEEDS EXPERIMENTATION
# Notice how multiple (failing) applications of this function will "converge" around the mean.
# More precisely, it will slightly oscillate around the convergence point.
def squeeze(regulator_dict, urn_list):
    '''
    This update function takes two arguments.
    
    regulator_dict: a regulator defined as a dictionary of key labels (plays or columns) 
    and integer values (from a distribution or urn).
    
    urn_list: a list of integers interpreted as the composition of a Polya urn.
    
    The function calculates the mean of the urn composition, and compares each value
    in the regulator_dict with the mean.  
    
    The resulting regulator_dict is updated by incrementing values smaller than the
    mean, and decrementing values greater than the mean.
    
    '''
    mean = np.mean(urn_list)
    for i in regulator_dict:
        if regulator_dict[i] >= mean:
            regulator_dict[i] -= 1
            #print('squeeze down:', regulator_dict[i])
        else:
            regulator_dict[i] += 1
            #print('squeeze up:', regulator_dict[i])



In [96]:
# Our new function which includes update protocols for both success and failure.
# Experiment with squeeze on/off and with magnitude of reinforcement for regulator action. 
# With squeeze on, it might need to be len(regulator_dict), whereas the sqrt of that might be sufficient without squeeze.
def update(regulator_dict,action,out,goal,urn_list,skweez=False):
    success = 0
    if out == goal:
        #print(action)
        #print("success: reinforced the regulator's action", action, "from", regulator_dict[action], "to", regulator_dict[action]+len(regulator_dict))
        regulator_dict[action] += len(regulator_dict)**(1/2)
        success += 1
        print("success!")
        #print('now we need to recalculate the probabilities according to the reinforced urn')
    elif skweez:
        print('fail: squeezing.')
        squeeze(regulator_dict, urn_list)
    return success


In [49]:
update(regulator,reg_action,out,goal,urn)

0

In [36]:
regulator


{1: 5, 2: 3, 3: 3, 4: 5, 5: 8, 6: 5, 7: 5, 8: 3, 9: 2, 10: 7, 11: 5, 12: 8}

In [37]:
prob_calc(regulator)

array([0.08474576, 0.05084746, 0.05084746, 0.08474576, 0.13559322,
       0.08474576, 0.08474576, 0.05084746, 0.03389831, 0.11864407,
       0.08474576, 0.13559322])

In [38]:
# original probabilities
probs

array([0.07017544, 0.03508772, 0.03508772, 0.10526316, 0.15789474,
       0.07017544, 0.07017544, 0.03508772, 0.01754386, 0.14035088,
       0.10526316, 0.15789474])

# Put it all together

In [97]:
# Now lets repetitively train a regulator on multiple disturbances from the environment.
# After each outcome, we will update, hoping to improve the likelihood of successful plays.
# This function incorporates most of what we have done separately above.

def train(game_size,goal,epochs,skweez):
    game = create_game(game_size)
    print(game)
    urn = np.random.randint(100, size=len(game.columns))
    probs = np.array([(i/sum(urn)) for i in urn])
    #print("probs:",probs)
    regulator = dict(zip(game.columns,urn))
    print("regulator:",regulator)
    dist = np.random.dirichlet(alpha=game.index)
    successes = 0
    i=1
    while i <= epochs:
        
        print("Epoch: ",i)
        
        # Environment chooses play.
        play = environment_play(game,dist)
        
        # Regulator chooses action.
        action = regulator_action(game,probs)
        
        # Compute state of the world that is output (index in game matrix)
        out = game.loc[play,action]
        #print("out:",out)
        
        # Update regulator.
        successes += update(regulator,action,out,goal,urn,skweez=skweez)
        print("successes per epoch:",successes / i)
        
        # Recalculate regulator probabilities.
        probs = prob_calc(regulator)
        #print("updated probs:",probs)
        
        
        #Increment i.
        i += 1
    return regulator

# Experiment
Notice the accuracy improvement when the regulator has access to more "plays" (columns).

In [100]:
trained_regulator = train(game_size=(10,500),goal=5,epochs=100000,skweez=False)

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
    1    2    3    4    5    6    7    8    9    10   ...  491  492  493  494  \
1     5    9    9    8    1    7    0    9    0    7  ...    7    4    5    7   
2     7    7    4    0    5    2    4    5    3    4  ...    4    0    0    5   
3     3    3    3    4    7    1    8    5    9    8  ...    2    9    4    6   
4     9    3    7    9    7    2    1    8    0    8  ...    3    5    1    0   
5     8    5    6    8    4    8    1    8    0    8  ...    1    8    6    3   
6     7    4    6    8    5    5    5    9    0    4  ...    5    5    4    4   
7     3    2    6    3    4    4    6    9    3    5  ...    0    4    3    1   
8     4    9    8    9    7    8    2    9    4    0  ...    2    0    4    7   
9     8    8    2    9    9    8    3    5    7    2  ...    2    8    0    8   
10    5    3    9    2    3    6    5    9    3    0  ...    8    5    8    6   

    495  496  497  498  499  500  
1     2    7    3    0    1    0  
2     

Epoch:  61
successes per epoch: 0.06557377049180328
Epoch:  62
successes per epoch: 0.06451612903225806
Epoch:  63
successes per epoch: 0.06349206349206349
Epoch:  64
successes per epoch: 0.0625
Epoch:  65
successes per epoch: 0.06153846153846154
Epoch:  66
successes per epoch: 0.06060606060606061
Epoch:  67
successes per epoch: 0.05970149253731343
Epoch:  68
successes per epoch: 0.058823529411764705
Epoch:  69
successes per epoch: 0.057971014492753624
Epoch:  70
successes per epoch: 0.05714285714285714
Epoch:  71
successes per epoch: 0.056338028169014086
Epoch:  72
successes per epoch: 0.05555555555555555
Epoch:  73
successes per epoch: 0.0547945205479452
Epoch:  74
successes per epoch: 0.05405405405405406
Epoch:  75
successes per epoch: 0.05333333333333334
Epoch:  76
successes per epoch: 0.05263157894736842
Epoch:  77
successes per epoch: 0.05194805194805195
Epoch:  78
successes per epoch: 0.05128205128205128
Epoch:  79
successes per epoch: 0.05063291139240506
Epoch:  80
successes pe

Epoch:  269
successes per epoch: 0.08550185873605948
Epoch:  270
successes per epoch: 0.08518518518518518
Epoch:  271
successes per epoch: 0.08487084870848709
Epoch:  272
successes per epoch: 0.08455882352941177
Epoch:  273
successes per epoch: 0.08424908424908426
Epoch:  274
successes per epoch: 0.08394160583941605
Epoch:  275
successes per epoch: 0.08363636363636363
Epoch:  276
successes per epoch: 0.08333333333333333
Epoch:  277
successes per epoch: 0.08303249097472924
Epoch:  278
successes per epoch: 0.08273381294964029
Epoch:  279
successes per epoch: 0.08243727598566308
Epoch:  280
successes per epoch: 0.08214285714285714
Epoch:  281
successes per epoch: 0.08185053380782918
Epoch:  282
successes per epoch: 0.08156028368794327
Epoch:  283
successes per epoch: 0.0812720848056537
Epoch:  284
successes per epoch: 0.08098591549295775
Epoch:  285
successes per epoch: 0.08070175438596491
Epoch:  286
successes per epoch: 0.08041958041958042
Epoch:  287
successes per epoch: 0.080139372822

Epoch:  459
successes per epoch: 0.10239651416122005
Epoch:  460
successes per epoch: 0.10217391304347827
Epoch:  461
successes per epoch: 0.1019522776572668
Epoch:  462
successes per epoch: 0.10173160173160173
Epoch:  463
successes per epoch: 0.10151187904967603
Epoch:  464
successes per epoch: 0.10129310344827586
Epoch:  465
success!
successes per epoch: 0.1032258064516129
Epoch:  466
successes per epoch: 0.10300429184549356
Epoch:  467
successes per epoch: 0.10278372591006424
Epoch:  468
successes per epoch: 0.10256410256410256
Epoch:  469
successes per epoch: 0.1023454157782516
Epoch:  470
successes per epoch: 0.10212765957446808
Epoch:  471
successes per epoch: 0.10191082802547771
Epoch:  472
successes per epoch: 0.1016949152542373
Epoch:  473
successes per epoch: 0.1014799154334038
Epoch:  474
successes per epoch: 0.10126582278481013
Epoch:  475
success!
successes per epoch: 0.1031578947368421
Epoch:  476
success!
successes per epoch: 0.10504201680672269
Epoch:  477
successes per

Epoch:  692
success!
successes per epoch: 0.11271676300578035
Epoch:  693
successes per epoch: 0.11255411255411256
Epoch:  694
successes per epoch: 0.11239193083573487
Epoch:  695
successes per epoch: 0.11223021582733812
Epoch:  696
successes per epoch: 0.11206896551724138
Epoch:  697
success!
successes per epoch: 0.1133428981348637
Epoch:  698
successes per epoch: 0.11318051575931232
Epoch:  699
successes per epoch: 0.11301859799713877
Epoch:  700
successes per epoch: 0.11285714285714285
Epoch:  701
successes per epoch: 0.11269614835948645
Epoch:  702
successes per epoch: 0.11253561253561253
Epoch:  703
successes per epoch: 0.112375533428165
Epoch:  704
successes per epoch: 0.11221590909090909
Epoch:  705
successes per epoch: 0.11205673758865248
Epoch:  706
successes per epoch: 0.11189801699716714
Epoch:  707
success!
successes per epoch: 0.11315417256011315
Epoch:  708
successes per epoch: 0.11299435028248588
Epoch:  709
successes per epoch: 0.11283497884344147
Epoch:  710
successes 

...

successes per epoch: 0.33259754266074004
Epoch:  99214
successes per epoch: 0.33259419033604126
Epoch:  99215
successes per epoch: 0.33259083807891954
Epoch:  99216
successes per epoch: 0.3325874858893727
Epoch:  99217
successes per epoch: 0.33258413376739876
Epoch:  99218
successes per epoch: 0.3325807817129956
Epoch:  99219
successes per epoch: 0.33257742972616133
Epoch:  99220
successes per epoch: 0.3325740778068938
Epoch:  99221
successes per epoch: 0.33257072595519094
Epoch:  99222
successes per epoch: 0.33256737417105076
Epoch:  99223
successes per epoch: 0.33256402245447125
Epoch:  99224
success!
successes per epoch: 0.33257074901233574
Epoch:  99225
successes per epoch: 0.3325673973293021
Epoch:  99226
success!
successes per epoch: 0.332574123717574
Epoch:  99227
successes per epoch: 0.33257077206808633
Epoch:  99228
successes per epoch: 0.3325674204861531
Epoch:  99229
success!
successes per epoch: 0.3325741466708321
Epoch:  99230
success!
successes per epoch: 0.33258087271994

Epoch:  99378
successes per epoch: 0.33260882690333876
Epoch:  99379
successes per epoch: 0.33260548003099244
Epoch:  99380
successes per epoch: 0.3326021332260012
Epoch:  99381
successes per epoch: 0.33259878648836294
Epoch:  99382
successes per epoch: 0.3325954398180757
Epoch:  99383
successes per epoch: 0.3325920932151374
Epoch:  99384
successes per epoch: 0.332588746679546
Epoch:  99385
success!
successes per epoch: 0.33259546209186497
Epoch:  99386
successes per epoch: 0.3325921155897209
Epoch:  99387
successes per epoch: 0.33258876915491964
Epoch:  99388
successes per epoch: 0.33258542278745923
Epoch:  99389
successes per epoch: 0.3325820764873376
Epoch:  99390
success!
successes per epoch: 0.3325887916289365
Epoch:  99391
successes per epoch: 0.33258544536225615
Epoch:  99392
successes per epoch: 0.3325820991629105
Epoch:  99393
successes per epoch: 0.33257875303089757
Epoch:  99394
successes per epoch: 0.33257540696621524
Epoch:  99395
successes per epoch: 0.3325720609688616
Ep

success!
successes per epoch: 0.33281096176641956
Epoch:  99547
success!
successes per epoch: 0.33281766401800156
Epoch:  99548
successes per epoch: 0.33281432072969824
Epoch:  99549
successes per epoch: 0.33281097750856364
Epoch:  99550
successes per epoch: 0.3328076343545957
Epoch:  99551
successes per epoch: 0.3328042912677924
Epoch:  99552
success!
successes per epoch: 0.33281099324975894
Epoch:  99553
success!
successes per epoch: 0.332817695097084
Epoch:  99554
success!
successes per epoch: 0.3328243968097716
Epoch:  99555
successes per epoch: 0.3328210536889157
Epoch:  99556
successes per epoch: 0.33281771063522037
Epoch:  99557
successes per epoch: 0.33281436764868366
Epoch:  99558
success!
successes per epoch: 0.3328210691255349
Epoch:  99559
successes per epoch: 0.3328177261724204
Epoch:  99560
successes per epoch: 0.3328143832864604
Epoch:  99561
success!
successes per epoch: 0.3328210845612238
Epoch:  99562
successes per epoch: 0.33281774170868406
Epoch:  99563
successes pe

successes per epoch: 0.33294891594295917
Epoch:  99719
success!
successes per epoch: 0.3329556052507546
Epoch:  99720
success!
successes per epoch: 0.3329622944243883
Epoch:  99721
success!
successes per epoch: 0.33296898346386417
Epoch:  99722
success!
successes per epoch: 0.33297567236918635
Epoch:  99723
success!
successes per epoch: 0.3329823611403588
Epoch:  99724
successes per epoch: 0.3329790221009988
Epoch:  99725
successes per epoch: 0.33297568312860365
Epoch:  99726
successes per epoch: 0.3329723442231715
Epoch:  99727
successes per epoch: 0.33296900538470026
Epoch:  99728
success!
successes per epoch: 0.33297569388737364
Epoch:  99729
successes per epoch: 0.33297235508227296
Epoch:  99730
successes per epoch: 0.3329690163441292
Epoch:  99731
success!
successes per epoch: 0.33297570464549636
Epoch:  99732
successes per epoch: 0.33297236594072116
Epoch:  99733
success!
successes per epoch: 0.3329790540743786
Epoch:  99734
success!
successes per epoch: 0.3329857420739166
Epoch:

successes per epoch: 0.33304636822295186
Epoch:  99897
successes per epoch: 0.3330430343253551
Epoch:  99898
successes per epoch: 0.3330397004945044
Epoch:  99899
successes per epoch: 0.3330363667303977
Epoch:  99900
success!
successes per epoch: 0.33304304304304305
Epoch:  99901
success!
successes per epoch: 0.3330497192220298
Epoch:  99902
successes per epoch: 0.3330463854577486
Epoch:  99903
success!
successes per epoch: 0.33305306146962554
Epoch:  99904
successes per epoch: 0.33304972773862906
Epoch:  99905
successes per epoch: 0.33304639407437064
Epoch:  99906
successes per epoch: 0.33304306047684823
Epoch:  99907
successes per epoch: 0.3330397269460598
Epoch:  99908
successes per epoch: 0.3330363934820034
Epoch:  99909
successes per epoch: 0.33303306008467704
Epoch:  99910
successes per epoch: 0.33302972675407866
Epoch:  99911
successes per epoch: 0.3330263934902063
Epoch:  99912
success!
successes per epoch: 0.3330330691008087
Epoch:  99913
success!
successes per epoch: 0.333039

In [101]:
trained_regulator

{1: 1926.575741549826,
 2: 12,
 3: 89,
 4: 63,
 5: 258.96747752497686,
 6: 60.3606797749979,
 7: 185.88543819998316,
 8: 56.721359549995796,
 9: 63,
 10: 278.246117974981,
 11: 166.08203932499367,
 12: 422.13155617496415,
 13: 77,
 14: 247.52475842498524,
 15: 45,
 16: 541.2956348249517,
 17: 56,
 18: 130.72135954999578,
 19: 76.36067977499789,
 20: 2251.3466179497937,
 21: 87,
 22: 6,
 23: 287.6067977499789,
 24: 661.3776741499455,
 25: 4,
 26: 2468.592735924776,
 27: 496.49223594996204,
 28: 76,
 29: 6624.400533624411,
 30: 409.41019662496836,
 31: 92,
 32: 50,
 33: 95,
 34: 2157.5432190748033,
 35: 0,
 36: 84,
 37: 2376.150016824784,
 38: 309.6067977499789,
 39: 7,
 40: 78,
 41: 131.08203932499367,
 42: 1180.7553482998912,
 43: 486.49223594996204,
 44: 342.6888370749726,
 45: 79,
 46: 54,
 47: 136.72135954999578,
 48: 56,
 49: 2,
 50: 162.08203932499367,
 51: 95,
 52: 19,
 53: 71.36067977499789,
 54: 63,
 55: 2102.543219074803,
 56: 0,
 57: 144.44271909999156,
 58: 616.0169943749476

In [95]:
25**(1/2)

5.0